# Modern portfolio theory of H. Markowitz

Modern portfolio theory is a practical method of selecting investments to maximise their overall return within an acceptable level of risk. This mathematical framework is used to construct a portfolio of investments that maximises the amount of expected return for a given level of collective risk — portfolio risk.

A key element of the LMP is diversification. Most investments are either high risk/high return or low risk/low return. According to Markowitz, investors can achieve the best results by choosing an optimal combination of these two types of investments based on an assessment of their individual risk tolerance.

In portfolio optimization we have some amount of money to invest in any of $n$ different assets. <br>
We choose what fraction $w_i$ of our money to invest in each asset $i$, $i=1, \ldots, n$.<br>
We call $w\in {\bf R}^n$ the **_portfolio allocation vector_**.<br>
We of course have the constraint that ${\mathbf 1}^T w =1$.
The allocation $w_i<0$ means a **short position** in asset $i$, or that we borrow shares to sell now that we must replace later.
The allocation $w \geq 0$ is a _long only_ portfolio.
The quantity
$$ \|w \|_1 = {\mathbf 1}^T w_+ + {\mathbf 1}^T w\_- $$
is known as _leverage_.

- Expected return: $$\mathbb{E}(r_p)=w^T\space \mathbb{E}(r) = \sum^{n}_{i=1}w_i\mathbb{E}(r_i)$$
- Risk (Annualized volatility $\sigma$ ) : $$\sigma^2_p=\sum^{n}_{i=1}\sum^{n}_{j=1}w_i\times w_j\times cov(r_i,r_j)$$
- The Sharpe Ratio from the CAPM: $$S_p=\frac{\mathbb{E}(r_p-r_f)}{\sigma_p}\space\text{basically}\space S_p=\frac{\mathbb{E}(r_p)-r_{f_{annualized}}}{\sigma_p}$$


In [7]:
from warnings import filterwarnings

filterwarnings("ignore")
from datetime import datetime
import pandas as pd
import numpy as np
import scipy.stats as stats
from scipy.optimize import minimize
from statsmodels.tsa.stattools import grangercausalitytests
import matplotlib.pyplot as plt

from quant_invest_lab.portfolio import MonteCarloPortfolio, ConvexPortfolio, RiskParityPortfolio
from quant_invest_lab.utils import get_cac40_symbols
from quant_invest_lab.data_provider import build_multi_crypto_dataframe, download_crypto_historical_data

In [8]:
MININUM_HISTORY_YEAR = 2
N = 365
# get_list_of_symbols()
symbols = set(
    [
        "ROSE-USDT",
        "AVAX-USDT",
        "UNI-USDT",
        "ATOM-USDT",
        "ICP-USDT",
        "THETA-USDT",
        "VET-USDT",
        "DOGE3S-USDT",
        "BNB-USDT",
        "NEAR-BTC",
        "BTC-USDT",
        "NEAR-USDT",
        "SOLVE-BTC",
        "ETH-USDT",
        "KDA-USDT",
        "SOL-USDT",
        "EGLD-USDT",
        "ALGO-USDT",
        "FTM-USDT",
        "AXS-USDT",
        "ADA-USDT",
        "NKN-USDT",
        "LOOM-BTC",
        "CUSD-USDT",
        "LTC3L-USDT",
        "XPR-USDT",
    ]
)


closes = build_multi_crypto_dataframe(symbols)

cols_to_remove = [
    col
    for col, nans in closes.isna().sum().items()
    if len(closes) - nans < int(N * MININUM_HISTORY_YEAR)
]


closes.drop(columns=cols_to_remove, inplace=True)
returns = closes.pct_change().dropna()
log_returns = np.log(closes).pct_change().dropna()
returns.head()

Fetching symbols...: 100%|██████████| 26/26 [00:02<00:00, 10.61it/s]


LOOM-BTC_Close  VET-USDT_Close  BNB-USDT_Close  ADA-USDT_Close  \
Date                                                                         
2021-05-13        0.000000        0.117686       -0.037427        0.240093   
2021-05-14        0.064935        0.022999        0.055260        0.040940   
2021-05-15       -0.012195       -0.075061       -0.063316        0.083025   
2021-05-16        0.053498        0.023313        0.000654        0.059594   
2021-05-17       -0.058594       -0.106909       -0.092994       -0.118150   

            ICP-USDT_Close  THETA-USDT_Close  BTC-USDT_Close  CUSD-USDT_Close  \
Date                                                                            
2021-05-13        0.174812          0.077174        0.000272        -0.000300   
2021-05-14        0.010374          0.024359        0.003485        -0.001002   
2021-05-15       -0.190680         -0.066774       -0.061649         0.002005   
2021-05-16       -0.085068          0.009101       -0.007440         0.001001   
2021-05-17       -0.129333          0.027947       -0.062220        -0.003199   

            ATOM-USDT_Close  ALGO-USDT_Close  ROSE-USDT_Close  UNI-USDT_Close  \
Date                                                                            
2021-05-13         0.026167         0.067230         0.005483        0.065836   
2021-05-14         0.102353         0.093419         0.012992        0.081661   
2021-05-15        -0.053575        -0.060050        -0.069432       -0.095644   
2021-05-16        -0.008590         0.006410         0.016250        0.001174   
2021-05-17        -0.131277        -0.080656        -0.086145       -0.089359   

            SOLVE-BTC_Close  ETH-USDT_Close  KDA-USDT_Close  AVAX-USDT_Close  \
Date                                                                           
2021-05-13        -0.025445       -0.023622       -0.105572         0.085266   
2021-05-14        -0.018277        0.096526       -0.005140         0.053091   
2021-05-15         0.053191       -0.105156       -0.061014        -0.067570   
2021-05-16        -0.020202       -0.017895       -0.102637         0.062339   
2021-05-17         0.216495       -0.083893       -0.112368        -0.078814   

            FTM-USDT_Close  
Date                        
2021-05-13        0.031130  
2021-05-14        0.116546  
2021-05-15       -0.112912  
2021-05-16        0.029127  
2021-05-17       -0.083341

In [9]:
portfolio = MonteCarloPortfolio(returns)


portfolio.fit(n_portfolios=20000, plot=True)
portfolio.get_allocation("sharpe", "max")

100%|██████████| 20000/20000 [00:37<00:00, 533.11it/s]


--------------  Results  ---------------
- Annualized Sharpe ratio: 0.47
- Annualized risk (volatility): 87.60 %
- Annualized expected return: 40.86 %


LOOM-BTC_Close  VET-USDT_Close  BNB-USDT_Close  ADA-USDT_Close  \
0        0.002395        0.011575        0.011899        0.069037   

   ICP-USDT_Close  THETA-USDT_Close  BTC-USDT_Close  CUSD-USDT_Close  \
0        0.008259          0.017505        0.030588         0.075777   

   ATOM-USDT_Close  ALGO-USDT_Close  ROSE-USDT_Close  UNI-USDT_Close  \
0         0.070653         0.024348         0.068472        0.013145   

   SOLVE-BTC_Close  ETH-USDT_Close  KDA-USDT_Close  AVAX-USDT_Close  \
0         0.136257        0.023953        0.139289          0.14861   

   FTM-USDT_Close  
0        0.148238

# Convex process


In [10]:
ptf = ConvexPortfolio(returns)
ptf.fit("sharpe", "max", max_asset_weight=0.2)
ptf.get_allocation()

--------------  Results  ---------------
- Annualized Sharpe ratio: 0.78
- Annualized risk (volatility): 73.68 %
- Annualized expected return: 57.11 %


LOOM-BTC_Close  VET-USDT_Close  BNB-USDT_Close  ADA-USDT_Close  \
0             0.2    1.500727e-14             0.0    5.120217e-15   

   ICP-USDT_Close  THETA-USDT_Close  BTC-USDT_Close  CUSD-USDT_Close  \
0    2.372095e-14      1.385239e-14             0.0              0.2   

   ATOM-USDT_Close  ALGO-USDT_Close  ROSE-USDT_Close  UNI-USDT_Close  \
0     8.945171e-14     1.185121e-14         0.066658    1.027725e-14   

   SOLVE-BTC_Close  ETH-USDT_Close  KDA-USDT_Close  AVAX-USDT_Close  \
0         0.133342             0.0             0.2     1.066128e-15   

   FTM-USDT_Close  
0             0.2

In [11]:
rp_ptf = RiskParityPortfolio(returns)
rp_ptf.fit()
rp_ptf.get_allocation()

--------------  Results  ---------------
- Annualized Sharpe ratio: 0.12
- Annualized risk (volatility): 26.09 %
- Annualized expected return: 3.25 %


LOOM-BTC_Close  VET-USDT_Close  BNB-USDT_Close  ADA-USDT_Close  \
0        0.037762        0.016417        0.022157         0.01948   

   ICP-USDT_Close  THETA-USDT_Close  BTC-USDT_Close  CUSD-USDT_Close  \
0        0.016457          0.016372        0.029285         0.683522   

   ATOM-USDT_Close  ALGO-USDT_Close  ROSE-USDT_Close  UNI-USDT_Close  \
0         0.015965         0.017596         0.015364        0.016672   

   SOLVE-BTC_Close  ETH-USDT_Close  KDA-USDT_Close  AVAX-USDT_Close  \
0         0.025937        0.020702        0.017033         0.015921   

   FTM-USDT_Close  
0        0.013358

## CAC40


In [12]:
import yfinance as yf

cac40_data = yf.download(get_cac40_symbols(), start="2013-01-01", end="2023-03-01")[
    "Adj Close"
]
returns = cac40_data.fillna(method="ffill").pct_change().dropna()
returns

[*********************100%***********************]  40 of 40 completed


ACA.PA     AI.PA    AIR.PA    ALO.PA     BN.PA    BNP.PA  \
Date                                                                     
2014-06-30 -0.028302  0.012008 -0.007101 -0.007085 -0.004770  0.002732   
2014-07-01  0.029612  0.010953 -0.020331 -0.011080  0.015671  0.036028   
2014-07-02 -0.004243 -0.000803 -0.013661 -0.013673 -0.003812 -0.006234   
2014-07-03  0.013731  0.015060  0.010044  0.004043  0.015306  0.004705   
2014-07-04 -0.006072  0.004945  0.004396  0.008629 -0.004846 -0.020488   
...              ...       ...       ...       ...       ...       ...   
2023-02-22 -0.020138 -0.008614 -0.000326 -0.003332  0.044924 -0.022018   
2023-02-23  0.007729 -0.006951  0.013520  0.000371 -0.013904  0.012977   
2023-02-24 -0.010807 -0.005653 -0.020090  0.018938 -0.002412 -0.013891   
2023-02-27  0.010396  0.026127  0.013941 -0.003280 -0.000372  0.024573   
2023-02-28  0.008197 -0.006860  0.003073  0.017550 -0.009488  0.010541   

               CA.PA    CAP.PA     CS.PA     DG.PA  ...       SNY      STLA  \
Date                                                ...                       
2014-06-30 -0.008100 -0.007241 -0.003141 -0.007994  ... -0.002626 -0.018812   
2014-07-01  0.013920  0.010557  0.006875 -0.002931  ...  0.002069  0.035318   
2014-07-02  0.020502  0.004368  0.000854 -0.001286  ... -0.001501 -0.009746   
2014-07-03  0.003049  0.054085  0.031836 -0.002943  ...  0.004699  0.033464   
2014-07-04 -0.007690 -0.017582 -0.002479 -0.002214  ...  0.000000  0.000000   
...              ...       ...       ...       ...  ...       ...       ...   
2023-02-22 -0.012111 -0.011813 -0.010672  0.002204  ...  0.008824  0.036615   
2023-02-23 -0.009473  0.006394  0.032362 -0.012828  ...  0.006039  0.043428   
2023-02-24  0.027286 -0.027901 -0.010449 -0.019491  ... -0.012627 -0.024972   
2023-02-27  0.004655  0.003410  0.033967  0.018364  ...  0.003145  0.002277   
2023-02-28  0.019896  0.007363  0.016170  0.002417  ... -0.020899 -0.005111   

                 STM     SU.PA    TEP.PA       TTE    URW.AS    VIE.PA  \
Date                                                                     
2014-06-30 -0.012222 -0.004921  0.010271  0.000000 -0.000705 -0.023166   
2014-07-01  0.046120 -0.001018  0.010613  0.007895  0.003060  0.015092   
2014-07-02 -0.003226 -0.009901  0.020451 -0.006184 -0.003754 -0.029026   
2014-07-03  0.007551  0.021029  0.010833 -0.003042 -0.001413 -0.001094   
2014-07-04  0.000000 -0.001728  0.006216  0.000000 -0.010377 -0.001825   
...              ...       ...       ...       ...       ...       ...   
2023-02-22 -0.005880  0.004313 -0.021974 -0.014514 -0.022595 -0.005614   
2023-02-23  0.022391  0.004945  0.007489  0.024761  0.033275  0.002823   
2023-02-24 -0.019422 -0.035349 -0.021518 -0.011371 -0.012034 -0.002815   
2023-02-27  0.015592  0.020268 -0.005198 -0.002716  0.025905  0.014467   
2023-02-28 -0.000830  0.000658 -0.011254 -0.008329  0.002341 -0.015304   

              VIV.PA    WLN.PA  
Date                            
2014-06-30 -0.008049  0.012195  
2014-07-01  0.014829 -0.012048  
2014-07-02 -0.010201 -0.006098  
2014-07-03  0.017827  0.006135  
2014-07-04 -0.006568 -0.003049  
...              ...       ...  
2023-02-22 -0.004883 -0.018196  
2023-02-23 -0.003067  0.010296  
2023-02-24 -0.004717 -0.038471  
2023-02-27  0.002473  0.022787  
2023-02-28  0.001850  0.023834  

[2241 rows x 40 columns]

In [13]:
ptf = ConvexPortfolio(returns)
ptf.fit("sharpe", "max", max_asset_weight=0.2)
alloc = ptf.get_allocation()

--------------  Results  ---------------
- Annualized Sharpe ratio: 1.44
- Annualized risk (volatility): 23.24 %
- Annualized expected return: 33.50 %


# Risk parity optimization


In [14]:
rp_ptf = RiskParityPortfolio(returns)
rp_ptf.fit()
rp_ptf.get_allocation()

--------------  Results  ---------------
- Annualized Sharpe ratio: 0.85
- Annualized risk (volatility): 21.95 %
- Annualized expected return: 18.66 %


ACA.PA     AI.PA    AIR.PA    ALO.PA     BN.PA    BNP.PA     CA.PA  \
0  0.018669  0.028795  0.017217  0.026927  0.037194  0.018068  0.033369   

     CAP.PA     CS.PA     DG.PA  ...       SNY      STLA       STM     SU.PA  \
0  0.022143  0.021225  0.021396  ...  0.042183  0.018114  0.019671  0.021029   

     TEP.PA       TTE    URW.AS    VIE.PA    VIV.PA    WLN.PA  
0  0.030463  0.025517  0.017969  0.024986  0.029998  0.024499  

[1 rows x 40 columns]

# Genetic algo

In [ ]:

import numpy as np

# Define the fitness function to maximize the Sharpe Ratio
def fitness_function(weights, data):
    data_returns = np.log(data) - np.log(data.shift(1))
    data_returns = data_returns.dropna()
    
    portfolio_returns = np.dot(data_returns, weights)
    portfolio_mean = np.mean(portfolio_returns)
    portfolio_std = np.std(portfolio_returns)
    sharpe_ratio = (portfolio_mean / portfolio_std) * np.sqrt(252)
    return sharpe_ratio

# Define the genetic algorithm
def genetic_algorithm(data, population_size=200, num_generations=50, mutation_rate=0.05, elitism=0.1):
    # Initialize the population
    population = np.random.rand(population_size, len(data.columns))
    population = population / np.sum(population, axis=1)[:, np.newaxis]

    # Calculate fitness of initial population
    fitness = np.array([fitness_function(individual, data) for individual in population])
    
    for generation in range(num_generations):
        # Sort the population by fitness
        sorted_idx = np.argsort(fitness)[::-1]
        population = population[sorted_idx]
        fitness = fitness[sorted_idx]
        
        # Determine number of individuals to carry over via elitism
        num_elites = int(elitism * population_size)
        
        # Create the next generation, starting with the elites
        offspring = population[:num_elites]
        
        # Select parents for reproduction using tournament selection
        parent1_idx = np.random.randint(num_elites, population_size, size=population_size-num_elites)
        parent2_idx = np.random.randint(num_elites, population_size, size=population_size-num_elites)
        parent1 = population[parent1_idx]
        parent2 = population[parent2_idx]

        # Perform crossover and mutation to create the next generation
        crossover_prob = np.random.rand(population_size-num_elites, len(data.columns))
        crossover_mask = crossover_prob <= 0.5
        offspring_crossover = np.where(crossover_mask, parent1, parent2)

        mutation_prob = np.random.rand(population_size-num_elites, len(data.columns))
        mutation_mask = mutation_prob <= mutation_rate
        mutation_values = np.random.rand(population_size-num_elites, len(data.columns))
        mutation_direction = np.random.choice([-1, 1], size=(population_size-num_elites, len(data.columns)))
        offspring_mutation = np.where(mutation_mask, offspring_crossover + mutation_direction * mutation_values, offspring_crossover)

        # Ensure the offspring population has valid weights
        offspring_mutation = offspring_mutation / np.sum(offspring_mutation, axis=1)[:, np.newaxis]

        # Combine elites and offspring to create the next generation
        population = np.vstack((population[:num_elites], offspring_mutation))
        
        # Calculate fitness of new population
        fitness = np.array([fitness_function(individual, data) for individual in population])
        
    # Return the best individual from the final population
    best_idx = np.argmax(fitness)
    best_individual = population[best_idx]
    print('Best Sharpe Ratio: ', np.max(fitness)) 

    return best_individual

from datetime import datetime, timedelta

# Seed for reproducibility
np.random.seed(42)

def backtest(genetic_algorithm, data, benchmark, initial_capital):
    # Split the data into training and testing sets
    train_data = data.iloc[:-252]
    test_data = data.iloc[-252:]

    # Run the genetic algorithm on the training set to find the optimal portfolio weights
    weights = genetic_algorithm(data=train_data, population_size=100, num_generations=50, mutation_rate=0.01, elitism=0.01)
    # print(weights)

    # Set any negative weights to 0
    weights[weights < 0] = 0

    # Normalize remaining positive weights to sum to 1
    weights /= weights.sum()

    # Calculate the returns of the portfolio and the benchmark on the test set
    portfolio_returns = np.dot(test_data.pct_change().dropna(), weights)
    portfolio_cum_returns = np.cumprod(1 + portfolio_returns)
    portfolio_value = initial_capital * portfolio_cum_returns[-1]
    benchmark_returns = benchmark.iloc[-252:].pct_change().dropna()
    benchmark_cum_returns = np.cumprod(1 + benchmark_returns)
    benchmark_value = initial_capital * benchmark_cum_returns[-1]

    # Calculate performance metrics
    portfolio_mean_return = np.mean(portfolio_returns)
    portfolio_std = np.std(portfolio_returns)
    portfolio_sharpe_ratio = (portfolio_mean_return / portfolio_std) * np.sqrt(252)
    benchmark_mean_return = np.mean(benchmark_returns)
    benchmark_std = np.std(benchmark_returns)
    benchmark_sharpe_ratio = (benchmark_mean_return / benchmark_std) * np.sqrt(252)

    # print(portfolio_cum_returns)

    # Visualize the performance of the portfolio and the benchmark
    fig, ax = plt.subplots(figsize=(12, 6))
    ax.plot(benchmark_cum_returns.index, portfolio_cum_returns, label='Portfolio')
    ax.plot(benchmark_cum_returns, label='Benchmark')
    ax.set_xlabel('Date')
    ax.set_ylabel('Cumulative Returns')
    ax.set_title('Backtesting Results')
    ax.legend()
    plt.show()

    # Print performance metrics
    print('Portfolio Statistics:')
    print('---------------------')
    print('Mean Daily Return: {:.4f}'.format(portfolio_mean_return))
    print('Standard Deviation: {:.4f}'.format(portfolio_std))
    print('Sharpe Ratio: {:.4f}'.format(portfolio_sharpe_ratio))
    print('Final Value: {:.2f}'.format(portfolio_value))
    print('')
    print('Benchmark Statistics:')
    print('---------------------')
    print('Mean Daily Return: {:.4f}'.format(benchmark_mean_return))
    print('Standard Deviation: {:.4f}'.format(benchmark_std))
    print('Sharpe Ratio: {:.4f}'.format(benchmark_sharpe_ratio))
    print('Final Value: {:.2f}'.format(benchmark_value))
    
    return portfolio_returns, benchmark_returns, portfolio_cum_returns, benchmark_cum_returns
    
portfolio_returns, benchmark_returns, portfolio_cum_returns, benchmark_cum_returns = backtest(genetic_algorithm, data, benchmark, initial_capital=1000)

# Using Riskfolio


In [ ]:
import riskfolio as rp

port = rp.Portfolio(returns=returns)

# Calculating optimal portfolio

# Select method and estimate input parameters:

method_mu = "hist"  # Method to estimate expected returns based on historical data.
method_cov = "hist"  # Method to estimate covariance matrix based on historical data.

port.assets_stats(method_mu=method_mu, method_cov=method_cov, d=0.94)

# Estimate optimal portfolio:

model = "Classic"  # Could be Classic (historical), BL (Black Litterman) or FM (Factor Model)
rm = "MV"  # Risk measure used, this time will be variance
obj = "Sharpe"  # Objective function, could be MinRisk, MaxRet, Utility or Sharpe
hist = True  # Use historical scenarios for risk measures that depend on scenarios
rf = 0  # Risk free rate
l = 0  # Risk aversion factor, only useful when obj is 'Utility'

w = port.optimization(model=model, rm=rm, obj=obj, rf=rf, l=l, hist=hist)

display(w.T)

In [ ]:
points = 50  # Number of points of the frontier

frontier = port.efficient_frontier(model=model, rm=rm, points=points, rf=rf, hist=hist)


label = "Max Risk Adjusted Return Portfolio"  # Title of point
mu = port.mu  # Expected returns
cov = port.cov  # Covariance matrix
returns = port.returns  # Returns of the assets

figure, ax = plt.subplots(1, 2, figsize=(15, 6))


rp.plot_frontier(
    w_frontier=frontier,
    mu=mu,
    cov=cov,
    returns=returns,
    rm=rm,
    rf=rf,
    alpha=0.05,
    cmap="viridis",
    w=w,
    label=label,
    marker="*",
    s=16,
    c="r",
    height=6,
    width=10,
    ax=ax[1],
)


rp.plot_pie(
    w=w,
    title="Sharpe Mean Variance",
    others=0.05,
    nrow=25,
    cmap="tab20",
    height=6,
    width=10,
    ax=ax[0],
)

In [ ]:
# Risk Measures available:
#
# 'MV': Standard Deviation.
# 'MAD': Mean Absolute Deviation.
# 'MSV': Semi Standard Deviation.
# 'FLPM': First Lower Partial Moment (Omega Ratio).
# 'SLPM': Second Lower Partial Moment (Sortino Ratio).
# 'CVaR': Conditional Value at Risk.
# 'EVaR': Entropic Value at Risk.
# 'WR': Worst Realization (Minimax)
# 'MDD': Maximum Drawdown of uncompounded cumulative returns (Calmar Ratio).
# 'ADD': Average Drawdown of uncompounded cumulative returns.
# 'CDaR': Conditional Drawdown at Risk of uncompounded cumulative returns.
# 'EDaR': Entropic Drawdown at Risk of uncompounded cumulative returns.
# 'UCI': Ulcer Index of uncompounded cumulative returns.
rms = [
    "MV",
    "MAD",
    "MSV",
    "FLPM",
    "SLPM",
    "CVaR",
    "EVaR",
    "WR",
    "MDD",
    "ADD",
    "CDaR",
    "UCI",
    "EDaR",
]

w_s = pd.DataFrame([])

for i in rms:
    w = port.optimization(model=model, rm=i, obj=obj, rf=rf, l=l, hist=hist)
    w_s = pd.concat([w_s, w], axis=1)

w_s.columns = rms


def filter_unused(x: pd.Series):
    for i in x:
        if i >= 1e-3:
            return True
    return False


w_s = w_s.loc[w_s.apply(filter_unused, axis=1)]
w_s.style.format("{:.2%}").background_gradient(cmap="YlGn")

## Comparing each portfolio


In [ ]:
fig = plt.gcf()
fig.set_figwidth(15)
fig.set_figheight(5)
ax = fig.subplots(nrows=1, ncols=1)

w_s.plot.bar(ax=ax)

# Using empyrical


In [ ]:
from empyrial import empyrial, Engine

portfolio = Engine(
    start_date="2018-01-01",  # start date for the backtesting
    portfolio=[
        "IRCTC.NS",
        "RELIANCE.NS",
        "INFY.NS",
        "HDFCBANK.NS",
    ],  # assets in your portfolio
    weights=[0.2, 0.2, 0.2, 0.2],  # equal weighting is set by default
    benchmark=["^NSEI"],  # SPY is set by default
)

empyrial(portfolio)